In [578]:
import pandas as pd
import numpy as np
import math
import TreeNode

# class TreeNode:
#     def __init__(self, label=None, attributes=None, children=None):
#         self.value = label  # value of the node
#         self.attributes = attributes if attributes is not None else {}  # attributes in dict
#         self.children = children or {}  # dict of child nodes
    
#     def add_child(self, child_value, child_node):
#         self.children[child_value] = child_node

#     def __str__(self, level=0):
#         prefix = "  " * level
#         result = prefix + f"Attribute: {self.attributes}, Label: {self.value}\n"
    
#         for child_value, child_node in self.children.items():
#             result += prefix + f"Value: {child_value}\n"
#             result += child_node.__str__(level + 1)
    
#         return result

# class TreeNode: 
#     def __init__(self, label=None, attributes=None, children=None):
#         self.value = label  # value of the node
#         self.attributes = attributes
#         self.children = children or []  # dict of child nodes
    
#     def __str__(self, level=0):
#         prefix = "  " * level
#         result = prefix + f"Attribute: {self.attributes}, Label: {self.value}\n"
#         for child in self.children:
#             result += prefix + f"Child:\n"
#             result += child.__str__(level + 1)
#         return result
#     # def __str__(self):
#     #     return str(self.value)

#     def add_child(self, child_node):
#         self.children.append(child_node)


def calculate_entropy(feature_value_data, class_list):
    """Function to calculate entropy"""
    # feature_value_data: Subdataset with feature value data
    # class_list: the unique class list in target variable
    feature_total_count = feature_value_data.shape[0]
    label_list = feature_value_data.iloc[:, -1].tolist()
    entropy = 0
    
    for class_label in class_list:
        class_count = label_list.count(class_label)
        class_probability = class_count / feature_total_count
        if class_probability > 0:
            class_entropy = -class_probability * math.log2(class_probability)
            entropy += class_entropy

    return entropy

def calculate_majority_error(feature_value_data, class_list):
    """Function to calculate majority error"""
    feature_total_count = feature_value_data.shape[0]
    label_list = feature_value_data.iloc[:, -1].tolist()
    majority_error = 0
    
    majority_class_count = max([label_list.count(c) for c in class_list])
    majority_error = 1 - (majority_class_count / feature_total_count)
    
    return majority_error

def calculate_gini_index(feature_value_data, class_list):
    """Function to calculate gini index"""
    feature_total_count = feature_value_data.shape[0]
    label_list = feature_value_data.iloc[:, -1].tolist()
    gini_index = 0
    
    for class_label in class_list:
        class_count = label_list.count(class_label)
        class_probability = class_count / feature_total_count
        gini_index += 1 - class_probability**2
    
    return gini_index


def calculate_info_gain(feature_name, data, class_list, purity_measurement):
    """Function to calculate information gain for a specfici feature/attribute"""
    # purity_measurement should be one of entropy, majority_error, gini
    feature_value_list = data[feature_name].unique()
    total_row = data.shape[0]
    feature_info = 0.0
    
    for feature_value in feature_value_list:
        feature_value_data = data[data[feature_name] == feature_value] #filtering rows with that feature_value
        feature_value_count = feature_value_data.shape[0]
        if purity_measurement == 'entropy':
            total_entropy = calculate_entropy(data, class_list)
            feature_value_entropy = calculate_entropy(feature_value_data, class_list) #calculcating entropy for the feature value
            feature_value_probability = feature_value_count/total_row
            feature_info += feature_value_probability * feature_value_entropy #calculating information of the feature value
            
        elif purity_measurement == 'majority_error':
            total_entropy = calculate_majority_error(data, class_list)
            feature_value_entropy = calculate_majority_error(feature_value_data, class_list) #calculcating entropy for the feature value
            feature_value_probability = feature_value_count/total_row
            feature_info += feature_value_probability * feature_value_entropy #calculating information of the feature value
        elif purity_measurement == 'gini':
            total_entropy = calculate_gini_index(data, class_list)
            feature_value_entropy = calculate_gini_index(feature_value_data, class_list) #calculcating entropy for the feature value
            feature_value_probability = feature_value_count/total_row
            feature_info += feature_value_probability * feature_value_entropy #calculating information of the feature value
        else: 
            print("No valid purity_measurement has been input. We only support entropy, majority_error and gini. Please further check! ")
            raise ValueError
    return total_entropy - feature_info


def find_best_attribute(data, attributes, class_list, purity_measurement):
    # Get the feature columns (all columns except the label column)
    max_info_gain = -1
    max_info_feature = None

    for attribute in attributes:  #for each feature in the dataset
        feature_info_gain = calculate_info_gain(attribute, data, class_list, purity_measurement)
        print("For {} the information gain is {}".format(attribute, feature_info_gain))
        if max_info_gain < feature_info_gain: #selecting feature name with highest information gain
            max_info_gain = feature_info_gain
            max_info_feature = attribute
            
    return max_info_feature

# Find most common label
def find_most_common_label(df):
    labels = df.iloc[:, -1].tolist()
    label_counts = count_elements(labels)
    most_common_label = max(label_counts, key=lambda k: label_counts[k])
    return most_common_label

def count_elements(lst):
    element_counts = {}
    for element in lst:
        if element in element_counts:
            element_counts[element] += 1
        else:
            element_counts[element] = 1
    return element_counts

# def ID3(S, Attributes, Label, max_depth=None, purity_measurement=None):
#     """
#     S is a dataframe of the dataset
#     Attributes are the value of the attributes
#     Label are the list of the target variable for the datase
#     Default purity measurement for ID3 is entropy
#     """ 
    
#     if not purity_measurement:
#         purity_measurement = 'entropy'  # Default purity measurement
#     print('Starting implementing ID3 with purity_measurement {}'.format(purity_measurement))

#     # Check if leaf mode with the same label
#     unique_labels = set(Label)
#     class_list = list(unique_labels)
#     if len(unique_labels) == 1:
#         print('unique labels == 1')
#         return TreeNode(label=unique_labels.pop())
#     # Check if attribute is empty
#     elif not Attributes:
#         most_common_label = find_most_common_label(S)
#         print("attibute is empty, find most common label: ", most_common_label)
#         return TreeNode(label=most_common_label)
#     else:
#         # Create a Root Node for tree
#         root = TreeNode()
#         print("------starting creating root node-------")
#         # Choose the best attribute A to split S
#         # find_most_informative_feature(data, class_list, purity_measurement):
#         best_attribute = find_best_attribute(S, class_list, purity_measurement)
#         print("best attribute: ", best_attribute)
#         root.attributes = best_attribute 
#         attribute_values = S[best_attribute].unique().tolist()
#         remaining_attributes = [attr for attr in Attributes if attr != best_attribute]
#         print("remaining_attributes: ", remaining_attributes)
        
#         # deal with the remaining attributes for subset Sv, according to A=V
#         for value in attribute_values:
#             print("value in attribute values:", value)
#             child_node = TreeNode()
#             child_node.attributes = value  
#             root.add_child(child_node) 
#             print("Check current root: ", root)

#             Sv = S[S[best_attribute] == value]
#             remaining_label = Sv.iloc[:,-1].tolist()
#             # If Sv is empty, add leaf node with the most common value of label in S
#             if Sv.empty:
#                 most_common_label = find_most_common_label(Sv)
#                 root.children.value = TreeNode(label=most_common_label)
#                 print("return root when Sv is empty",root)
#             else:
#                 return ID3(Sv, remaining_attributes, remaining_label, purity_measurement)
#     return root

In [579]:
# def ID3(S, Attributes, Label, max_depth=None, purity_measurement=None, root=None):
#     """
#     S is a dataframe of the dataset
#     Attributes are the value of the attributes
#     Label are the list of the target variable for the dataset
#     Default purity measurement for ID3 is entropy
#     """ 
    
#     if not purity_measurement:
#         purity_measurement = 'entropy'  # Default purity measurement
#     print('Starting implementing ID3 with purity_measurement {}'.format(purity_measurement))

#     # Check if leaf mode with the same label
#     unique_labels = set(Label)
#     class_list = list(unique_labels)
#     print("class_list check: ", class_list)
#     if len(unique_labels) == 1:
#         print('unique labels == 1')
#         if root is None:
#             return TreeNode(label=unique_labels.pop())
#         else:
#             root.label = unique_labels.pop()
#             return root
#     # Check if attribute is empty
#     elif not Attributes:
#         most_common_label = find_most_common_label(S)
#         print("attribute is empty, find most common label: ", most_common_label)
#         if root is None:
#             return TreeNode(label=most_common_label)
#         else:
#             root.label = most_common_label
#             return root
#     else:
#         if root is None:
#             print("----root is None, first time to create tree node")
#             root = TreeNode()
#         # Choose the best attribute A to split S
#         # find_most_informative_feature(data, class_list, purity_measurement):
#         print("class_list check: ", class_list)
#         best_attribute = find_best_attribute(S, class_list, purity_measurement)
#         print("best attribute: ", best_attribute)
#         root.attributes = best_attribute 
#         attribute_values = S[best_attribute].unique().tolist()
#         remaining_attributes = [attr for attr in Attributes if attr != best_attribute]
#         print("remaining_attributes: ", remaining_attributes)
#         # deal with the remaining attributes for subset Sv, according to A=V
#         for value in attribute_values:
#             print("value in attribute values:", value)
#             child_node = TreeNode()
#             child_node.attributes = value  
#             root.add_child(child_node) 
#             print("Check current root: ", root)

#             Sv = S[S[best_attribute] == value]
#             remaining_label = Sv.iloc[:,-1].tolist()
#             # If Sv is empty, add leaf node with the most common value of label in S
#             if Sv.empty:
#                 most_common_label = find_most_common_label(Sv)
#                 child_node.label = most_common_label
#                 print("return root when Sv is empty",root)
#             else:
#                 ID3(Sv, remaining_attributes, remaining_label, purity_measurement, root=root)
#     return root


In [580]:
# test2 -!! this one work!!

# class TreeNode: 
#     def __init__(self, label=None, value=None, attributes=None, children=None):
#         self.label = label  # value of the node
#         self.value = value
#         self.attributes = attributes
#         self.children = children or []  # dict of child nodes
    
#     def __str__(self, level=0):
#         prefix = "  " * level
#         result = prefix + f"Attribute: {self.attributes},Value: {self.value}, Label: {self.label}\n"
#         for child in self.children:
#             result += prefix + f"Child:\n"
#             result += child.__str__(level + 1)
#         return result
#     # def __str__(self):
#     #     return str(self.value)

#     def add_child(self, child_node):
#         self.children.append(child_node)
        
# def ID3(S, Attributes, max_depth, purity_measurement=None, root=None):
#     if not purity_measurement:
#         purity_measurement = 'entropy'  # Default purity measurement
#     # Check if leaf mode with the same label
#     Label = S.iloc[:,-1].tolist()
#     unique_labels = set(Label)
#     class_list = list(unique_labels)  
#     if len(unique_labels) == 1:
#         get_unique_label = next(iter(unique_labels))
#         if root is None:
#             return TreeNode(label=get_unique_label)
#         else:
#             root.label = get_unique_label
#             return root
    
#     # Check if attribute is empty
#     elif not Attributes or max_depth==0:
#         most_common_label = find_most_common_label(S)
#         if root is None:
#             return TreeNode(label=most_common_label)
#         else:
#             root.label = most_common_label
#             return root
    
#     else:
#         if root is None:
#             root = TreeNode()
#             print("------Root is none, first time creating root node-------")
#         print("------starting creating root node-------")
#         # Choose the best attribute A to split S
#         print("check current root:", root)
        
#         best_attribute = find_best_attribute(S, Attributes, class_list, purity_measurement)
#         print("best attribute: ", best_attribute)
#         root.attributes = best_attribute

#         # Create a new list for remaining attributes
#         remaining_attributes = [attr for attr in Attributes if attr != best_attribute]
#         print("remaining_attributes: ", remaining_attributes)  
#         # Deal with the remaining attributes for subset Sv, according to A=V
#         attribute_values = S[best_attribute].unique().tolist()
        
#         for value in attribute_values:
#             print("value in attribute values:", value)
#             child_node = TreeNode()
#             root.value = value  
#             root.add_child(child_node) 
#             print("Check current root: ", root)

#             Sv = S[S[best_attribute] == value]
            
#             # If Sv is empty, add leaf node with the most common value of label in S
#             if Sv.empty:
#                 most_common_label = find_most_common_label(Sv)
#                 child_node.label = most_common_label
                
#                 print("check child node: ", child_node)
#             else:
#                 print("starting create sub tree")
#                 ID3(Sv, remaining_attributes, max_depth-1, purity_measurement, root=child_node)
#     return root


In [581]:
#TEST3 works for splitting sunny attributes etc
class TreeNode: 
    def __init__(self, label=None, attributes=None, children=None):
        self.label = label  # value of the node
        self.attributes = attributes
        if children == None:
            self.children = []
        else:
            self.children = children
    
    def __str__(self, level=0):
        prefix = "  " * level
        result = prefix + f"Attribute: {self.attributes}, Label: {self.label}\n"
        for child in self.children:
            result += prefix + f"Child:\n"
            result += child.__str__(level + 1)
        return result
    # def __str__(self):
    #     return str(self.value)

    def add_child(self, child_node):
        self.children.append(child_node)

    def move_to_next_node(self, matched_child):
        self.current_node = matched_child  
        
def ID3(S, Attributes, max_depth, purity_measurement=None, root=None):
    if not purity_measurement:
        purity_measurement = 'entropy'  # Default purity measurement
    # Check if leaf mode with the same label
    Label = S.iloc[:,-1].tolist()
    unique_labels = set(Label)
    class_list = list(unique_labels)  
    if len(unique_labels) == 1:
        get_unique_label = next(iter(unique_labels))
        if root is None:
            return TreeNode(label=get_unique_label)
        else:
            root.label = get_unique_label
            return root
    
    # Check if attribute is empty
    elif not Attributes or max_depth==0:
        most_common_label = find_most_common_label(S)
        if root is None:
            return TreeNode(label=most_common_label)
        else:
            root.label = most_common_label
            return root
    
    else:
        if root is None:
            root = TreeNode()
        # Choose the best attribute A to split S
        best_attribute = find_best_attribute(S, Attributes, class_list, purity_measurement)
        if root.attributes == None:
            next_node = root
            next_node.attributes = best_attribute
        else:
            next_node = TreeNode()
            next_node.attributes = best_attribute
            root.add_child(next_node)
        
        # Create a new list for remaining attributes
        remaining_attributes = [attr for attr in Attributes if attr != best_attribute]
        # Deal with the remaining attributes for subset Sv, according to A=V
        attribute_values = S[best_attribute].unique().tolist()
        
        for value in attribute_values:
            child_node = TreeNode()
            child_node.attributes = value  
            next_node.add_child(child_node) 
            Sv = S[S[best_attribute] == value]
            
            # If Sv is empty, add leaf node with the most common value of label in S
            if Sv.empty:
                most_common_label = find_most_common_label(Sv)
                child_node.label = most_common_label
            else:
                ID3(Sv, remaining_attributes, max_depth-1, purity_measurement, root=child_node)
    return root

In [582]:
# #TEST3 works for splitting sunny attributes etc
# class TreeNode: 
#     def __init__(self, label=None, value=None, attributes=None, children=None):
#         self.label = label  # value of the node
#         self.value = value
#         self.attributes = attributes
#         if children == None:
#             self.children = []
#         else:
#             self.children = children
    
#     def __str__(self, level=0):
#         prefix = "  " * level
#         result = prefix + f"Attribute: {self.attributes}, Value: {self.value}, Label: {self.label}\n"
#         for child in self.children:
#             result += prefix + f"Child:\n"
#             result += child.__str__(level + 1)
#         return result
#     # def __str__(self):
#     #     return str(self.value)

#     def add_child(self, child_node):
#         self.children.append(child_node)
        
# def ID3(S, Attributes, max_depth, purity_measurement=None, root=None):
#     if not purity_measurement:
#         purity_measurement = 'entropy'  # Default purity measurement
#     # Check if leaf mode with the same label
#     Label = S.iloc[:,-1].tolist()
#     unique_labels = set(Label)
#     class_list = list(unique_labels)  
#     if len(unique_labels) == 1:
#         get_unique_label = next(iter(unique_labels))
#         if root is None:
#             return TreeNode(label=get_unique_label)
#         else:
#             root.label = get_unique_label
#             return root
    
#     # Check if attribute is empty
#     elif not Attributes or max_depth==0:
#         most_common_label = find_most_common_label(S)
#         if root is None:
#             return TreeNode(label=most_common_label)
#         else:
#             root.label = most_common_label
#             return root
    
#     else:
#         if root is None:
#             root = TreeNode()
#             print("------Root is none, first time creating root node-------")
#         print("------starting creating root node-------")
#         # Choose the best attribute A to split S
#         print("check current root:", root)
#         best_attribute = find_best_attribute(S, Attributes, class_list, purity_measurement)
#         print("best attribute: ", best_attribute)
#         root.attributes = best_attribute
#         # if root.attributes == None:
#         #     next_node = root
#         #     next_node.attributes = best_attribute
#         # else:
#         #     next_node = TreeNode()
#         #     next_node.attributes = best_attribute
#         #     root.add_child(next_node)
        
#         # Create a new list for remaining attributes
#         remaining_attributes = [attr for attr in Attributes if attr != best_attribute]
#         print("remaining_attributes: ", remaining_attributes)  
#         # Deal with the remaining attributes for subset Sv, according to A=V
#         attribute_values = S[best_attribute].unique().tolist()
        
#         for value in attribute_values:
#             print("value in attribute values:", value)
#             child_node = TreeNode()
#             root.value = value  
#             root.add_child(child_node) 
#             print("Check current root: ", root)
#             print("check child node: ", child_node)

#             Sv = S[S[best_attribute] == value]
            
#             # If Sv is empty, add leaf node with the most common value of label in S
#             if Sv.empty:
#                 most_common_label = find_most_common_label(Sv)
#                 child_node.label = most_common_label
                
#                 print("check child node: ", child_node)
#             else:
#                 print("starting create sub tree")
#                 ID3(Sv, remaining_attributes, max_depth-1, purity_measurement, root=child_node)
#     return root

In [583]:
# Sample Usage
S = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "-"},
]

df_S = pd.DataFrame(S)

Attributes = ["Outlook", "Temperature", "Humidity", "Wind"]
Label = ["-", "-", "+", "+", "+", "-", "+", "-", "+", "+", "+", "+", "+", "-"]
Target_var = 'Play'


# root = ID3(df_S, Attributes, Label, purity_measurement='entropy')  # You can change purity_measurement as needed
# root1 = ID3(df_S, Attributes, max_depth=1, purity_measurement='entropy')
root2 = ID3(df_S, Attributes, max_depth=2, purity_measurement='majority_error')

For Outlook the information gain is 0.07142857142857134
For Temperature the information gain is 0.0
For Humidity the information gain is 0.07142857142857134
For Wind the information gain is 0.0
For Temperature the information gain is 0.2
For Humidity the information gain is 0.4
For Wind the information gain is 0.0
For Temperature the information gain is 0.0
For Humidity the information gain is 0.0
For Wind the information gain is 0.4


In [484]:
print(root1)

Attribute: Outlook, Label: None
Child:
  Attribute: Sunny, Label: -
Child:
  Attribute: Overcast, Label: +
Child:
  Attribute: Rain, Label: +



In [533]:
print(root2)

Attribute: Outlook, Label: None
Child:
  Attribute: Sunny, Label: None
  Child:
    Attribute: Humidity, Label: None
    Child:
      Attribute: High, Label: -
    Child:
      Attribute: Normal, Label: +
Child:
  Attribute: Overcast, Label: +
Child:
  Attribute: Rain, Label: None
  Child:
    Attribute: Wind, Label: None
    Child:
      Attribute: Weak, Label: +
    Child:
      Attribute: Strong, Label: -



In [429]:
print(root2)

Attribute: Outlook, Label: None
Child:
  Attribute: Sunny, Label: None
  Child:
    Attribute: Humidity, Label: None
    Child:
      Attribute: High, Label: -
    Child:
      Attribute: Normal, Label: +
Child:
  Attribute: Overcast, Label: +
Child:
  Attribute: Rain, Label: None
  Child:
    Attribute: Wind, Label: None
    Child:
      Attribute: Weak, Label: +
    Child:
      Attribute: Strong, Label: -



In [431]:
# Sample Usage
S_test = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
]

df_test = pd.DataFrame(S_test)

In [495]:
# def predict(tree, test_data):

#     while tree.children:
#         current_attribute = tree.attributes
#         attribute_value = test_data.get(current_attribute)

#         matched_child = None
#         for child in tree.children:
#             if child.attributes == attribute_value:
#                 matched_child = child
#                 break

#         if matched_child:
#             tree = matched_child
#         else:
#             return tree.label
        
#     return tree.label


#Only work when depth =1, because will raise key error when finding attribute =sunny
# def predict(tree, df_test):
#     predictions = []
#     for index, row in df_test.iterrows():
#         node = tree
#         while node.children:  # 只要还有子节点就继续预测
#             attribute_value = row[node.attributes]  # 获取当前节点的属性值
#             for child in node.children:
#                 if child.attributes == attribute_value:  # 找到与示例匹配的子节点
#                     node = child  # 移动到下一个节点
#                     break
#         predictions.append(node.label)  # 到达叶子节点，将叶子节点的标签作为预测结果

#     return predictions

# for child in root2.children:
#     print("Attribute:", child.attributes)
#     print("Label:", child.label)
#     # 继续检查子节点的子节点（如果有的话）
#     for grandchild in child.children:
#         print("  Grandchild Attribute:", grandchild.attributes)
#         print("  Grandchild Label:", grandchild.label)

# This works!!!!!!!!!!!!!!!!!
def predict(tree, df_test):
    predictions = []
    for index, row in df_test.iterrows():
        print("row :",row)
        node = tree
        while node.children:  # 只要还有子节点就继续预测
            attribute_name = node.attributes  # 获取当前节点的属性名
            print("tree node attribute_name: ", attribute_name)
            attribute_value = row[attribute_name]  # 获取当前示例的属性值
            print("test data attribute_value: ", attribute_value)
            matched_child = None
            for child in node.children:
                print("node.children: ", child)
                if child.attributes == attribute_value:  # 找到与示例匹配的子节点
                    print("child.attribute=attribute.value")
                    matched_child = child  # 移动到下一个节点
                    print("matched child before break: ", matched_child)
                    break
            if matched_child:
                node = matched_child
                print("node == matched_child: ", node)
                for subnode in node.children:
                    node = subnode
            else:
                break
        predictions.append(node.label)  # 到达叶子节点，将叶子节点的标签作为预测结果

    return predictions

# 示例用法
# predictions = predict(root1, df_test)
# print("预测结果:", predictions)


# 示例用法
predictions = predict(root2, df_test)
print("预测结果:", predictions)



row : Outlook        Sunny
Temperature      Hot
Humidity        High
Wind            Weak
Play               +
Name: 0, dtype: object
tree node attribute_name:  Outlook
test data attribute_value:  Sunny
node.children:  Attribute: Sunny, Label: None
Child:
  Attribute: Humidity, Label: None
  Child:
    Attribute: High, Label: -
  Child:
    Attribute: Normal, Label: +

child.attribute=attribute.value
matched child before break:  Attribute: Sunny, Label: None
Child:
  Attribute: Humidity, Label: None
  Child:
    Attribute: High, Label: -
  Child:
    Attribute: Normal, Label: +

node == matched_child:  Attribute: Sunny, Label: None
Child:
  Attribute: Humidity, Label: None
  Child:
    Attribute: High, Label: -
  Child:
    Attribute: Normal, Label: +

tree node attribute_name:  Humidity
test data attribute_value:  High
node.children:  Attribute: High, Label: -

child.attribute=attribute.value
matched child before break:  Attribute: High, Label: -

node == matched_child:  Attribute: Hi

In [494]:
true_labels = df_test.iloc[:, -1].tolist()
print(true_labels)

error_rate = calculate_error_rate(predictions, true_labels)
print(error_rate)

['+', '-', '+', '+', '+', '-', '+', '-', '+', '+', '-', '+', '+', '-']
0.21428571428571427


In [439]:
def make_predictions(tree_root, test_data):
    predictions = []
    for index, row in test_data.iterrows():
        prediction = predict(tree_root, row)  
        predictions.append(prediction)
    return predictions


['+', '-', '+', '+', '+', '-', '+', '-', '+', '+', '-', '+', '+', '-']


0.2857142857142857


In [423]:
# Sample Usage
# Sample Usage
S = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
]

df_train = pd.DataFrame(S)

Attributes = ["Outlook", "Temperature", "Humidity", "Wind"]

# root = ID3(df_S, Attributes, Label, purity_measurement='entropy')  # You can change purity_measurement as needed
# root = ID3(df_S, Attributes, max_depth=1, purity_measurement='entropy')

S_test = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
]

df_test = pd.DataFrame(S_test)

In [424]:
# run tree and make prediction and cal error
root = ID3(df_train, Attributes, max_depth=1, purity_measurement='entropy')
predictions = make_predictions(root, df_test)
true_labels = df_test.iloc[:, -1].tolist()
error_rate = calculate_error_rate(predictions, true_labels)

------Root is none, first time creating root node-------
------starting creating root node-------
check current root: Attribute: None, Label: None

starting finding the best feature
data count for input df:  14
feature list in find best_attribute ['Outlook', 'Temperature', 'Humidity', 'Wind']
For Outlook the information gain is 0.24674981977443933
For Temperature the information gain is 0.02922256565895487
For Humidity the information gain is 0.15183550136234159
For Wind the information gain is 0.003184853044648994
best attribute:  Outlook
remaining_attributes:  ['Temperature', 'Humidity', 'Wind']
value in attribute values: Sunny
Check current root:  Attribute: None, Label: None
Child:
  Attribute: Sunny, Label: None

check child node:  Attribute: Sunny, Label: None

starting create sub tree
value in attribute values: Overcast
Check current root:  Attribute: None, Label: None
Child:
  Attribute: Sunny, Label: -
Child:
  Attribute: Overcast, Label: None

check child node:  Attribute: Ov

In [425]:
print(error_rate)

1.0


In [307]:
max_depths = range(1, 7)
# column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
# df_train, attributes = read_data("Data/car-4/train.csv", column_names)
# df_test, attributes = read_data("Data/car-4/test.csv", column_names)

for max_depth in max_depths:
    print(f"Testing with max_depth = {max_depth}")
    
    root = ID3(df_S, Attributes, max_depth=max_depth, purity_measurement='entropy')
    
    testing_predictions = make_predictions(root, df_test)
    testing_true_labels = df_test.iloc[:, -1].tolist()
    testing_error_rate = calculate_error_rate(testing_predictions, testing_true_labels)

    print(f"Testing Error Rate with max_depth {max_depth}: {testing_error_rate}")

Testing with max_depth = 1
Starting implementing ID3 with purity_measurement entropy
class list in this iteration ['+', '-']
------Root is none, first time creating root node-------
------starting creating root node-------
starting finding the best feature
data count for input df:  14
feature list in find best_attribute ['Outlook', 'Temperature', 'Humidity', 'Wind']
For Outlook the information gain is 0.24674981977443933
For Temperature the information gain is 0.02922256565895487
For Humidity the information gain is 0.15183550136234159
For Wind the information gain is 0.003184853044648994
best attribute:  Outlook
remaining_attributes:  ['Temperature', 'Humidity', 'Wind']
value in attribute values: Sunny
Check current root:  Attribute: Outlook, Label: None
Child:
  Attribute: Sunny, Label: None

Starting implementing ID3 with purity_measurement entropy
class list in this iteration ['+', '-']
attribute is empty, find most common label:  -
value in attribute values: Overcast
Check current

In [254]:
true_labels = df_test.iloc[:, -1].tolist()

In [303]:
def read_data(file_path, column_names):
    # Read the CSV file with the specified column names
    df = pd.read_csv(file_path, names=column_names)
    # Extract the list of attributes from the DataFrame's columns and drop the last column (label)
    attributes = df.columns.tolist()[:-1]
    return df, attributes

true_labels = df_test.iloc[:, -1].tolist()
print(true_labels)

error_rate = calculate_error_rate(predictions, true_labels)
print(error_rate)

def calculate_error_rate(predictions, true_labels):
    """
    predictions: list of prediction labels using ID3
    true_labels: real labels
    error_rate
    """
    if len(predictions) != len(true_labels):
        raise ValueError("Number of predictions and true label do not match")

    incorrect_predictions = 0
    total_samples = len(predictions)

    for i in range(total_samples):
        if predictions[i] != true_labels[i]:
            incorrect_predictions += 1

    error_rate = incorrect_predictions / total_samples
    return error_rate

In [304]:
max_depths = range(1, 7)
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
df_train, attributes = read_data("Data/car-4/train.csv", column_names)
df_test, attributes = read_data("Data/car-4/test.csv", column_names)

for max_depth in max_depths:
    print(f"Testing with max_depth = {max_depth}")
    
    root = ID3(df_train, attributes, max_depth=max_depth, purity_measurement='entropy')
    
    testing_predictions = make_predictions(root, df_test)
    testing_true_labels = df_test.iloc[:, -1].tolist()
    testing_error_rate = calculate_error_rate(testing_predictions, testing_true_labels)

    print(f"Testing Error Rate with max_depth {max_depth}: {testing_error_rate}")


Testing with max_depth = 1
Starting implementing ID3 with purity_measurement entropy
class list in this iteration ['good', 'vgood', 'acc', 'unacc']
------Root is none, first time creating root node-------
------starting creating root node-------
starting finding the best feature
data count for input df:  1000
feature list in find best_attribute ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']
For buying the information gain is 0.10152470712485662
For maint the information gain is 0.07741985577459665
For doors the information gain is 0.006726514230977809
For persons the information gain is 0.22441128678577127
For lug_boot the information gain is 0.03688725199484155
For safety the information gain is 0.25822501448993573
best attribute:  safety
remaining_attributes:  ['buying', 'maint', 'doors', 'persons', 'lug_boot']
value in attribute values: med
Check current root:  Attribute: safety, Label: None
Child:
  Attribute: med, Label: None

Starting implementing ID3 with purity_m

In [255]:
def calculate_error_rate(predictions, true_labels):
    """
    predictions: list of prediction labels using ID3
    true_labels: real labels
    error_rate
    """
    if len(predictions) != len(true_labels):
        raise ValueError("Number of predictions and true label do not match")

    incorrect_predictions = 0
    total_samples = len(predictions)

    for i in range(total_samples):
        if predictions[i] != true_labels[i]:
            incorrect_predictions += 1

    error_rate = incorrect_predictions / total_samples
    return error_rate

In [256]:
# Calculate testing error
testing_predictions = predictions
testing_true_labels = df_test.iloc[:, -1].tolist()

testing_error_rate = calculate_error_rate(testing_predictions, testing_true_labels)
print("Testing Error Rate:", testing_error_rate)

Testing Error Rate: 0.2857142857142857


In [259]:
# Read data
df_car_train = pd.read_csv("Data/car-4/train.csv")

In [260]:
df_car_train.head()

low vhigh      4 4.1    big   med    acc
0    low  high  5more   4    med  high  vgood
1  vhigh   med      2   2    big  high  unacc
2   high  high      2   2  small  high  unacc
3  vhigh   low      3   2    big   low  unacc
4   high  high      3   4    med   low  unacc

In [261]:
df_car_train.columns.tolist()

['low', 'vhigh', '4', '4.1', 'big', 'med', 'acc']

In [262]:
import pandas as pd

# Define the column names as a list
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
# Read the CSV file with the specified column names
df_car_train = pd.read_csv("Data/car-4/train.csv", names=column_names)

df_car_train.head()

buying  maint  doors persons lug_boot safety  label
0    low  vhigh      4       4      big    med    acc
1    low   high  5more       4      med   high  vgood
2  vhigh    med      2       2      big   high  unacc
3   high   high      2       2    small   high  unacc
4  vhigh    low      3       2      big    low  unacc

In [264]:
car_attributes = df_car_train.columns.tolist()

In [273]:
# Function of read data
import pandas as pd

def read_data(file_path, column_names):
    # Read the CSV file with the specified column names
    df = pd.read_csv(file_path, names=column_names)
    # Extract the list of attributes from the DataFrame's columns
    attributes = df.columns.tolist()[:-1]
    return df, attributes

# Example usage:
file_path = "Data/car-4/train.csv"
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
df_car_train, car_attributes = read_data(file_path, column_names)


In [274]:
df_car_train.head()

buying  maint  doors persons lug_boot safety  label
0    low  vhigh      4       4      big    med    acc
1    low   high  5more       4      med   high  vgood
2  vhigh    med      2       2      big   high  unacc
3   high   high      2       2    small   high  unacc
4  vhigh    low      3       2      big    low  unacc

In [275]:
print(car_attributes)

['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']


In [276]:
test_file_path = "Data/car-4/test.csv"
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
df_car_test, car_attributes = read_data(file_path, column_names)

In [277]:
root = ID3(df_car_train, car_attributes, max_depth=1, purity_measurement='entropy')

Starting implementing ID3 with purity_measurement entropy
class list in this iteration ['good', 'vgood', 'acc', 'unacc']
------Root is none, first time creating root node-------
------starting creating root node-------
starting finding the best feature
data count for input df:  1000
feature list in find best_attribute ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']
For buying the information gain is 0.10152470712485662
For maint the information gain is 0.07741985577459665
For doors the information gain is 0.006726514230977809
For persons the information gain is 0.22441128678577127
For lug_boot the information gain is 0.03688725199484155
For safety the information gain is 0.25822501448993573
best attribute:  safety
remaining_attributes:  ['buying', 'maint', 'doors', 'persons', 'lug_boot']
value in attribute values: med
Check current root:  Attribute: safety, Label: None
Child:
  Attribute: med, Label: None

Starting implementing ID3 with purity_measurement entropy
class li

In [278]:
print(root)

Attribute: safety, Label: None
Child:
  Attribute: med, Label: unacc
Child:
  Attribute: high, Label: unacc
Child:
  Attribute: low, Label: unacc



In [496]:
#Read Data
test_file_path = "Data/car-4/test.csv"
train_file_path = "Data/car-4/test.csv"
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
df_car_train = pd.read_csv(train_file_path, names=column_names)
df_car_test = pd.read_csv(test_file_path, names=column_names)
car_attributes = df_car_train.columns.tolist()[:-1]

In [497]:
# Make tree
root1 = ID3(df_car_train, car_attributes, max_depth=1, purity_measurement='entropy')
root2 = ID3(df_car_train, car_attributes, max_depth=2, purity_measurement='entropy')
root3 = ID3(df_car_train, car_attributes, max_depth=3, purity_measurement='entropy')

------Root is none, first time creating root node-------
------starting creating root node-------
check current root: Attribute: None, Label: None

starting finding the best feature
data count for input df:  728
feature list in find best_attribute ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']
For buying the information gain is 0.09283999511527607
For maint the information gain is 0.07485756090384799
For doors the information gain is 0.00867820859928825
For persons the information gain is 0.22348463119783513
For lug_boot the information gain is 0.027990402043574614
For safety the information gain is 0.26928929525031386
best attribute:  safety
remaining_attributes:  ['buying', 'maint', 'doors', 'persons', 'lug_boot']
value in attribute values: low
Check current root:  Attribute: safety, Label: None
Child:
  Attribute: low, Label: None

check child node:  Attribute: low, Label: None

starting create sub tree
value in attribute values: med
Check current root:  Attribute: sa

In [563]:
def predict(tree, df_test):
    predictions = []
    for index, row in df_test.iterrows():
        node = tree
        while node.children:  
            attribute_name = node.attributes  
            attribute_value = row[attribute_name] 
            matched_child = None
            for child in node.children:
                if child.attributes == attribute_value:  # 找到与示例匹配的子节点
                    matched_child = child  # 移动到下一个节点
                    break
            if matched_child:
                node = matched_child
                for subnode in node.children:
                    node = subnode
            else:
                break
        predictions.append(node.label)  # 到达叶子节点，将叶子节点的标签作为预测结果

    return predictions


def calculate_error_rate(predictions, true_labels):
    """
    predictions: list of prediction labels using ID3
    true_labels: real labels
    error_rate
    """
    if len(predictions) != len(true_labels):
        raise ValueError("Number of predictions and true label do not match")

    incorrect_predictions = 0
    total_samples = len(predictions)

    for i in range(total_samples):
        if predictions[i] != true_labels[i]:
            incorrect_predictions += 1

    error_rate = incorrect_predictions / total_samples
    return error_rate

In [505]:
# Make predictions
predictions = predict(root1, df_car_test)
true_labels = df_car_test.iloc[:, -1].tolist()
error_rate = calculate_error_rate(predictions, true_labels)
print(error_rate)

0.2967032967032967


In [507]:
# Make predictions
predictions = predict(root2, df_car_test)
true_labels = df_car_test.iloc[:, -1].tolist()
error_rate = calculate_error_rate(predictions, true_labels)
print(error_rate)

0.22115384615384615


In [508]:
# Make predictions
predictions = predict(root3, df_car_test)
true_labels = df_car_test.iloc[:, -1].tolist()
error_rate = calculate_error_rate(predictions, true_labels)
print(error_rate)

0.1662087912087912


In [564]:
test_file_path = "Data/car-4/test.csv"
train_file_path = "Data/car-4/train.csv"
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
df_car_train = pd.read_csv(train_file_path, names=column_names)
df_car_test = pd.read_csv(test_file_path, names=column_names)
car_attributes = df_car_train.columns.tolist()[:-1]

In [565]:
# Cacluate error rate in depth from 1 to 6 for entropy

max_depths = [1, 2, 3, 4, 5, 6]
error_rates = []

for max_depth in max_depths:
    root = ID3(df_car_train, car_attributes, max_depth=max_depth, purity_measurement='entropy')
    predictions = predict(root, df_car_test)
    true_labels = df_car_test.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")


Max Depth 1: Error Rate 0.2967032967032967
Max Depth 2: Error Rate 0.22252747252747251
Max Depth 3: Error Rate 0.19642857142857142
Max Depth 4: Error Rate 0.14697802197802198
Max Depth 5: Error Rate 0.1043956043956044
Max Depth 6: Error Rate 0.125


In [566]:
# Cacluate error rate in depth from 1 to 6 for entropy - Training

max_depths = [1, 2, 3, 4, 5, 6]
error_rates = []

for max_depth in max_depths:
    root = ID3(df_car_train, car_attributes, max_depth=max_depth, purity_measurement='entropy')
    predictions = predict(root, df_car_train)
    true_labels = df_car_train.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")


Max Depth 1: Error Rate 0.302
Max Depth 2: Error Rate 0.222
Max Depth 3: Error Rate 0.181
Max Depth 4: Error Rate 0.082
Max Depth 5: Error Rate 0.027
Max Depth 6: Error Rate 0.0


In [567]:
# Cacluate error rate in depth from 1 to 6 for majority_error

max_depths = [1, 2, 3, 4, 5, 6]
error_rates = []

for max_depth in max_depths:
    root = ID3(df_car_train, car_attributes, max_depth=max_depth, purity_measurement='majority_error')
    predictions = predict(root, df_car_test)
    true_labels = df_car_test.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")

Max Depth 1: Error Rate 0.2967032967032967
Max Depth 2: Error Rate 0.3159340659340659
Max Depth 3: Error Rate 0.2623626373626374
Max Depth 4: Error Rate 0.24313186813186813
Max Depth 5: Error Rate 0.17994505494505494
Max Depth 6: Error Rate 0.19917582417582416


In [568]:
# Cacluate error rate in depth from 1 to 6 for majority_error - Training

max_depths = [1, 2, 3, 4, 5, 6]
error_rates = []

for max_depth in max_depths:
    root = ID3(df_car_train, car_attributes, max_depth=max_depth, purity_measurement='majority_error')
    predictions = predict(root, df_car_train)
    true_labels = df_car_train.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")


Max Depth 1: Error Rate 0.302
Max Depth 2: Error Rate 0.301
Max Depth 3: Error Rate 0.242
Max Depth 4: Error Rate 0.13
Max Depth 5: Error Rate 0.043
Max Depth 6: Error Rate 0.0


In [569]:
# Cacluate error rate in depth from 1 to 6 for gini

max_depths = [1, 2, 3, 4, 5, 6]
error_rates = []

for max_depth in max_depths:
    root = ID3(df_car_train, car_attributes, max_depth=max_depth, purity_measurement='gini')
    predictions = predict(root, df_car_test)
    true_labels = df_car_test.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")

Max Depth 1: Error Rate 0.2967032967032967
Max Depth 2: Error Rate 0.22252747252747251
Max Depth 3: Error Rate 0.18406593406593408
Max Depth 4: Error Rate 0.13324175824175824
Max Depth 5: Error Rate 0.1043956043956044
Max Depth 6: Error Rate 0.125


In [570]:
# Cacluate error rate in depth from 1 to 6 for gini - Training

max_depths = [1, 2, 3, 4, 5, 6]
error_rates = []

for max_depth in max_depths:
    root = ID3(df_car_train, car_attributes, max_depth=max_depth, purity_measurement='gini')
    predictions = predict(root, df_car_train)
    true_labels = df_car_train.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")


Max Depth 1: Error Rate 0.302
Max Depth 2: Error Rate 0.222
Max Depth 3: Error Rate 0.176
Max Depth 4: Error Rate 0.089
Max Depth 5: Error Rate 0.027
Max Depth 6: Error Rate 0.0


BANK DATASET

In [584]:
test_file_path = "Data/bank-4/test.csv"
train_file_path = "Data/bank-4/train.csv"
column_names = ['age', 'job', 'marital', 'education', 'default', 'balance', 'housing', 'loan', 'contact', 'day', 'month', 'duration', 'campaign', 'pdays', 'previous', 'poutcome']
df_bank_train = pd.read_csv(train_file_path, names=column_names)
df_bank_test = pd.read_csv(test_file_path, names=column_names)
bank_attributes = df_bank_train.columns.tolist()[:-1]

In [587]:
df_bank_train.head()

age      job    marital education  default balance housing  \
41     services  married  secondary        no        0     yes      no   
48  blue-collar   single  secondary        no      312     yes     yes   
55   technician  married  secondary        no     1938      no     yes   
54       admin.  married   tertiary        no       59     yes      no   
34   management   single   tertiary        no     2646      no      no   

        loan  contact  day  month  duration  campaign  pdays previous poutcome  
41   unknown        5  may    114         2        -1      0  unknown       no  
48  cellular        3  feb    369         2        -1      0  unknown       no  
55  cellular       18  aug    193         1       386      3  success      yes  
54  cellular       10  jul    268         1        -1      0  unknown       no  
34  cellular       14  apr    142         1        -1      0  unknown      yes

In [586]:
df_bank_train.dtypes

age          object
job          object
marital      object
education    object
default       int64
balance      object
housing      object
loan         object
contact       int64
day          object
month         int64
duration      int64
campaign      int64
pdays         int64
previous     object
poutcome     object
dtype: object

In [592]:
import pandas as pd
import numpy as np

# Covert numerical value to categorical value
df_bank_train1 = df_bank_train.copy()
numerical_columns = ["default", "contact", "month", "duration", "campaign", "pdays"]

# Deal with unknown in numerical columns
for column in numerical_columns:
    df_bank_train1[column] = df_bank_train1[column].replace('unknown', np.nan)

# Calculate medians with exsiting numerical value in numerical columns
medians = df_bank_train1[numerical_columns].median(skipna=False)

# Assign Low and High to replace numerical values
for column in numerical_columns:
    df_bank_train1[column] = pd.cut(df_bank_train1[column], bins=[float("-inf"), medians[column], float("inf")], labels=["Low", "High"])

for column in numerical_columns:
    df_bank_train1[column] = df_bank_train1[column].cat.add_categories("unknown").fillna("unknown")

df_bank_train1.head()


age      job    marital education default balance housing  \
41     services  married  secondary        no     Low     yes      no   
48  blue-collar   single  secondary        no     Low     yes     yes   
55   technician  married  secondary        no    High      no     yes   
54       admin.  married   tertiary        no     Low     yes      no   
34   management   single   tertiary        no    High      no      no   

        loan contact  day month duration campaign pdays previous poutcome  
41   unknown     Low  may   Low      Low      Low   Low  unknown       no  
48  cellular     Low  feb  High      Low      Low   Low  unknown       no  
55  cellular    High  aug  High      Low     High  High  success      yes  
54  cellular     Low  jul  High      Low      Low   Low  unknown       no  
34  cellular     Low  apr   Low      Low      Low   Low  unknown      yes

In [593]:
import pandas as pd
import numpy as np

def preprocess_numerical_columns(df, numerical_columns):
    # Covert numerical value to categorical value
    df_processed = df.copy()

    # Deal with unknown in numerical columns
    for column in numerical_columns:
        df_processed[column] = df_processed[column].replace('unknown', np.nan)

    # Calculate medians with exsiting numerical value in numerical columns
    medians = df_processed[numerical_columns].median(skipna=False)

    # Assign Low and High to replace numerical values
    for column in numerical_columns:
        df_processed[column] = pd.cut(df_processed[column], bins=[float("-inf"), medians[column], float("inf")], labels=["Low", "High"])
    for column in numerical_columns:
        df_processed[column] = df_processed[column].cat.add_categories("unknown").fillna("unknown")

    return df_processed

# 使用示例
numerical_columns = ["default", "contact", "month", "duration", "campaign", "pdays"]
df_all_categorical_bank_train = preprocess_numerical_columns(df_bank_train, numerical_columns)
df_all_categorical_bank_test = preprocess_numerical_columns(df_bank_test, numerical_columns)


In [594]:
# Cacluate error rate in depth from 1 to 6 for entropy - testing data

max_depths = range(1, 17)
error_rates = []

for max_depth in max_depths:
    root = ID3(df_all_categorical_bank_train, bank_attributes, max_depth=max_depth, purity_measurement='entropy')
    predictions = predict(root, df_all_categorical_bank_test)
    true_labels = df_all_categorical_bank_test.iloc[:, -1].tolist()
    error_rate = calculate_error_rate(predictions, true_labels)
    error_rates.append(error_rate)
for depth, error_rate in zip(max_depths, error_rates):
    print(f"Max Depth {depth}: Error Rate {error_rate}")


For age the information gain is 0.013310658043091506
For job the information gain is 0.004521422949425591
For marital the information gain is 0.00662615102787778
For education the information gain is 0.0007237854700455904
For default the information gain is 0.0037189338644761927
For balance the information gain is 0.013953305731499666
For housing the information gain is 0.004852394810047511
For loan the information gain is 0.0181130321424543
For contact the information gain is 0.0008070074610829758
For day the information gain is 0.03646957704202258
For month the information gain is 0.05960230138776085
For duration the information gain is 0.004091706003924167
For campaign the information gain is 0.013693126997486704
For pdays the information gain is 0.013693126997486704
For previous the information gain is 0.03964955279086224
For age the information gain is 0.013310658043091506
For job the information gain is 0.004521422949425591
For marital the information gain is 0.00662615102787778


In [279]:
# make predictions
predictions = []
for index, row in df_car_test.iterrows():
    prediction = predict(root, row)  
    predictions.append(prediction)

# Calculate testing error
testing_predictions = predictions
testing_true_labels = df_car_test.iloc[:, -1].tolist()

testing_error_rate = calculate_error_rate(testing_predictions, testing_true_labels)
print("Testing Error Rate:", testing_error_rate) 

Testing Error Rate: 0.302


In [320]:
# Define the column names as a list
column_names = ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety', 'label']
# Read the CSV file with the specified column names
df_car_train = pd.read_csv("Data/car-4/train.csv", names=column_names)
df_car_test  = pd.read_csv("Data/car-4/test.csv", names=column_names)
car_attributes = column_names[:-1]
print(car_attributes)

['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']


In [321]:
# run tree and make prediction and cal error
root = ID3(df_car_train, car_attributes, max_depth=1, purity_measurement='entropy')
predictions = make_predictions(root, df_car_test)
true_labels = df_car_test.iloc[:, -1].tolist()
error_rate = calculate_error_rate(predictions, true_labels)

Starting implementing ID3 with purity_measurement entropy
class list in this iteration ['good', 'vgood', 'acc', 'unacc']
------Root is none, first time creating root node-------
------starting creating root node-------
starting finding the best feature
data count for input df:  1000
feature list in find best_attribute ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']
For buying the information gain is 0.10152470712485662
For maint the information gain is 0.07741985577459665
For doors the information gain is 0.006726514230977809
For persons the information gain is 0.22441128678577127
For lug_boot the information gain is 0.03688725199484155
For safety the information gain is 0.25822501448993573
best attribute:  safety
remaining_attributes:  ['buying', 'maint', 'doors', 'persons', 'lug_boot']
value in attribute values: med
Check current root:  Attribute: safety, Label: None
Child:
  Attribute: med, Label: None

Starting implementing ID3 with purity_measurement entropy
class li

In [322]:
print(error_rate)

0.2967032967032967


In [324]:
# run tree and make prediction and cal error
root = ID3(df_car_train, car_attributes, max_depth=2, purity_measurement='entropy')
predictions = make_predictions(root, df_car_test)
true_labels = df_car_test.iloc[:, -1].tolist()
error_rate = calculate_error_rate(predictions, true_labels)

Starting implementing ID3 with purity_measurement entropy
class list in this iteration ['good', 'vgood', 'acc', 'unacc']
------Root is none, first time creating root node-------
------starting creating root node-------
starting finding the best feature
data count for input df:  1000
feature list in find best_attribute ['buying', 'maint', 'doors', 'persons', 'lug_boot', 'safety']
For buying the information gain is 0.10152470712485662
For maint the information gain is 0.07741985577459665
For doors the information gain is 0.006726514230977809
For persons the information gain is 0.22441128678577127
For lug_boot the information gain is 0.03688725199484155
For safety the information gain is 0.25822501448993573
best attribute:  safety
remaining_attributes:  ['buying', 'maint', 'doors', 'persons', 'lug_boot']
value in attribute values: med
Check current root:  Attribute: safety, Label: None
Child:
  Attribute: med, Label: None

Starting implementing ID3 with purity_measurement entropy
class li

In [325]:
print(error_rate)

0.6607142857142857


In [229]:
# Sample test for TreeNode Class
class TreeNode: 
    def __init__(self, label=None, attributes=None, children=None):
        self.label = label  # value of the node
        self.attributes = attributes
        self.children = children or []  # dict of child nodes
    
    def __str__(self, level=0):
        prefix = "  " * level
        result = prefix + f"Attribute: {self.attributes}, Label: {self.label}\n"
        for child in self.children:
            result += prefix + f"Child:\n"
            result += child.__str__(level + 1)
        return result
    # def __str__(self):
    #     return str(self.value)

    def add_child(self, child_node):
        self.children.append(child_node)

# tree = TreeNode()
# tree.attributes = {}
# tree.attributes = "Outlook"
# child_node = TreeNode()
# child_node.attributes = 'Sunny'

# tree.add_child(child_node)
# print(tree)
import random

tree = TreeNode()
tree.attributes = "Outlook"
print(tree)

Label = ["-", "-"]
unique_labels = set(Label)
print("unique_labels: ", unique_labels)
label_list = list(unique_labels)
random_label = random.choice(label_list)

attribute_values = ['Sunny','Overcast', 'Rain']
for value in attribute_values:
    child_node = TreeNode()
    child_node.attributes = value  
    tree.add_child(child_node) 
    grand_child = TreeNode()
    grand_child.attributes = "Humidity"
    child_node.add_child(grand_child)

    child_node.label = random_label
    tree.add_child(child_node)


print("print tree", tree)

Attribute: Outlook, Label: None

unique_labels:  {'-'}
print tree Attribute: Outlook, Label: None
Child:
  Attribute: Sunny, Label: -
  Child:
    Attribute: Humidity, Label: None
Child:
  Attribute: Sunny, Label: -
  Child:
    Attribute: Humidity, Label: None
Child:
  Attribute: Overcast, Label: -
  Child:
    Attribute: Humidity, Label: None
Child:
  Attribute: Overcast, Label: -
  Child:
    Attribute: Humidity, Label: None
Child:
  Attribute: Rain, Label: -
  Child:
    Attribute: Humidity, Label: None
Child:
  Attribute: Rain, Label: -
  Child:
    Attribute: Humidity, Label: None



In [166]:
df_S = pd.DataFrame(S)

best_attribute = 'Outlook'
value = 'Sunny'
Sv = df_S[df_S[best_attribute] == value]
remaining_label = Sv.iloc[:,-1].tolist()

print(remaining_label)
print(Sv)

['-', '-', '-', '+', '+']
   Outlook Temperature Humidity    Wind Play
0    Sunny         Hot     High    Weak    -
1    Sunny         Hot     High  Strong    -
7    Sunny        Mild     High    Weak    -
8    Sunny        Cool   Normal    Weak    +
10   Sunny        Mild   Normal  Strong    +


In [94]:
root = TreeNode()
root.attributes = "Outlook"
attribute_list = ["Sunny", "Rain"]
for value in attribute_list:
    child_node = TreeNode()
    child_node.attributes = value
    root.add_child(child_node)
print(root)

Attribute: Outlook, Label: None
Child:
  Attribute: Sunny, Label: None
Child:
  Attribute: Rain, Label: None



In [79]:
# Sample Usage
S = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
]

df_S = pd.DataFrame(S)

# Find most common label
def find_most_common_label(df):
    labels = df.iloc[:, -1].tolist()
    label_counts = count_elements(labels)
    print("label_counts: ", label_counts)
    most_common_label = max(label_counts, key=lambda k: label_counts[k])
    return most_common_label

def count_elements(lst):
    element_counts = {}
    for element in lst:
        if element in element_counts:
            element_counts[element] += 1
        else:
            element_counts[element] = 1
    return element_counts

test_common_label = find_most_common_label(df_S)
print(test_common_label)

# np.bincount(df_S.iloc[:, -1].tolist()).argmax()

label_counts:  {'-': 5, '+': 9}
+


In [102]:
# Sample Usage
S = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
]

df_S = pd.DataFrame(S)

Attributes = ["Outlook", "Temperature", "Humidity", "Wind"]
Label = ["-", "-", "+", "+", "+", "-", "+", "-", "+", "+", "+", "+", "+", "-"]
Target_var = 'Play'


root = ID3(df_S, Attributes, Label, purity_measurement='entropy')  # You can change purity_measurement as needed

purity_measurement: entropy
starting create root node
starting finding the most informative feature
starting calculating Outlook information gain
starting feature_value=Sunny in the list
starting feature_value=Overcast in the list
starting feature_value=Rain in the list
For Outlook the information gain is 0.24674981977443933
starting calculating Temperature information gain
starting feature_value=Hot in the list
starting feature_value=Mild in the list
starting feature_value=Cool in the list
For Temperature the information gain is 0.02922256565895487
starting calculating Humidity information gain
starting feature_value=High in the list
starting feature_value=Normal in the list
For Humidity the information gain is 0.15183550136234159
starting calculating Wind information gain
starting feature_value=Weak in the list
starting feature_value=Strong in the list
For Wind the information gain is 0.003184853044648994
max info feature:  Outlook
best attribute:  Outlook
attribute_values:  ['Sunny'

In [103]:
print(root)

Attribute: {}, Label: -



In [41]:
root.attributes

{}

In [98]:
# Sample Usage
S = [
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Hot", "Humidity": "High", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "-"},
    {"Outlook": "Overcast", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
    {"Outlook": "Sunny", "Temperature": "Cool", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Sunny", "Temperature": "Mild", "Humidity": "Normal", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Mild", "Humidity": "High", "Wind": "Strong", "Play": "+"},
    {"Outlook": "Overcast", "Temperature": "Hot", "Humidity": "Normal", "Wind": "Weak", "Play": "+"},
    {"Outlook": "Rain", "Temperature": "Mild", "Humidity": "High", "Wind": "Weak", "Play": "-"},
]

df_S = pd.DataFrame(S)

attribute_values = df_S['Outlook'].unique().tolist()
# attribute_values_str = ', '.join(attribute_values)
# print(attribute_values_str)
print(attribute_values)

['Sunny', 'Overcast', 'Rain']
